# Yelp API - Lab



## Introduction 

Now that we've seen how the Yelp API works, it's time to put those API and SQL skills to work in order to do some basic business analysis! Taking things a step further, you'll also independently explore how to perform pagination in order to retrieve a full results set from the Yelp API!

## Objectives

You will be able to:
* Create a DB on AWS to store information from Yelp about businesses
* Create HTTP requests to get data from Yelp API
* Parse HTTP responses and insert the information into your DB
* Perform pagination to retrieve troves of data!
* Write SQL queries to answer questions about your data 

## Problem Introduction

For this lab you will analyze the yelp data for a group of businesses to learn more about an industry. You will choose a type of business (Italian Restuarants, Nail Salons, Crossfit gyms) and a location to analyze. Then you will get data from the Yelp API, store that data in a SQL Database on AWS, and write queries to answer questions about the data. 


### Process:

1. Read through the SQL questions and the API documentation to determine which pieces of information you need to pull from the Yelp API.

2. Create a DB schema with 2 tables. One for the businesses and one for the reviews.

3. Create code to:
  - Perform a search of businesses using pagination
  - Parse the API response for specific data points
  - Insert the data into your AWS DB

4. Use the functions above in a loop that will paginate over the results to retrieve all of the results. 

5. Create functions to:
  - Retrieve the reviews data of one business
  - Parse the reviews response for specific review data
  - Insert the review data into the DB

6. Using SQL, query all of the business IDs. Using the 3 Python functions you've created, run your business IDs through a loop to get the reviews for each business and insert them into your DB.

7. Write SQL queries to answer the following questions about your data.


Bonus Steps:  
- Place your helper functions in a package so that your final notebook only has the major steps listed.
- Rewrite your business search functions to be able take an argument for the type of business you are searching for.
- Add another group of businesses to your database.


 
## SQL Questions:

- Which are the 5 most reviewed businesses?
- What is the highest rating recieved in your data set and how many businesses have that rating?
- What percentage of businesses have a rating greater than or  4.5?
- What percentage of businesses have a rating less than 3?
- What is the average rating of restaurants that have a price label of one dollar sign? Two dollar signs? Three dollar signs? 
- Return the text of the reviews for the most reviewed restaurant. 
- Return the name of the business with the most recent review. 
- Find the highest rated business and return text of the most recent review. If multiple business have the same rating, select the restaurant with the most reviews. 
- Find the lowest rated business and return text of the most recent review.  If multiple business have the same rating, select the restaurant with the least reviews. 


## Part 1 - Understanding your data and question

Lok at the question and determine what data you will need to store in your database in order to answer the questions. Start to thin about your DB schema. What tables will you want to create and what columns will you ahve for those tables. 

Look at the API documentation, and determine what fields of the API response you will match up with the columns you want in your DB tables. 


https://www.yelp.com/developers/documentation/v3/get_started

## Part 2 - Set up the DB

Now that you are familiar with the data, create your SQL queries to create the DB and the appropriate tables. 

### Foriegn Keys

For this project you will have two tables that you need to link using a foreign key. Below is some information about how to create a foriegn key.  

http://www.mysqltutorial.org/mysql-foreign-key/



### Using DB:
    
For this lab, you can either store the data on one DB or put in on both of the partners DBs. If you decide to put it on one DB, you want to make sure both partners have access to it.  To do this you want to add a user to your DB.  

[how to add a new user](https://howchoo.com/g/mtm3zdq2nzv/how-to-add-a-mysql-user-and-grant-privileges)

In [1]:
## Connect to DB server on AWS
import requests
import json
API_KEY= 'yeI9-k9bd44eW7rDikeLxRJ-nwwDkLwKzC9O7Dpzg7V1DzNOejqso1aWUSn7fK1yAWf-nh_7QTdcw8jvuIQ9MqO5DmPMqQZhnABlt3ZZEDDqrqXQLvP50_sSXAIqXnYx'
headers={'Authorization':'bearer %s'% API_KEY}

In [2]:
## Create new DB 
def businessCallGET(args):
    businessEndpoint = 'https://api.yelp.com/v3/businesses/search'
    return requests.get(businessEndpoint, params=args,headers=headers)

In [3]:
# Create a table for the Businesses
#from page 1 to 1000 
offset=list(range(0,1000,50))
business_data=[]
for i in offset:
    b_params={'term':'pizza','location':'New York City','limit':50,'offset':i}
    business_data.append(businessCallGET(b_params).json())



In [4]:
b_data= business_data.copy()
b_data

[{'businesses': [{'id': 'ysqgdbSrezXgVwER2kQWKA',
    'alias': 'julianas-pizza-brooklyn-5',
    'name': "Juliana's Pizza",
    'image_url': 'https://s3-media2.fl.yelpcdn.com/bphoto/clscwgOF9_Ecq-Rwsq7jyQ/o.jpg',
    'is_closed': False,
    'url': 'https://www.yelp.com/biz/julianas-pizza-brooklyn-5?adjust_creative=H-RlZ0bPhg3dmTEOOsLJMg&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=H-RlZ0bPhg3dmTEOOsLJMg',
    'review_count': 2161,
    'categories': [{'alias': 'pizza', 'title': 'Pizza'}],
    'rating': 4.5,
    'coordinates': {'latitude': 40.7026153030093,
     'longitude': -73.9934159993549},
    'transactions': [],
    'price': '$$',
    'location': {'address1': '19 Old Fulton St',
     'address2': '',
     'address3': '',
     'city': 'Brooklyn',
     'zip_code': '11201',
     'country': 'US',
     'state': 'NY',
     'display_address': ['19 Old Fulton St', 'Brooklyn, NY 11201']},
    'phone': '+17185966700',
    'display_phone': '(718) 596-6700',
    'distanc

In [5]:
#'id', 'name', 'price','phone','review_count', 'rating', 'location', , 
business_id=[]
name=[]
review_count=[]
rating=[]
street=[]
state=[]
zip_code=[]
country=[]
for i in b_data:
    for j in i['businesses']:
        business_id.append(j['id'])
        name.append(j['name'])
        review_count.append(j['review_count'])
        rating.append(j['rating'])
        street.append(j['location']['address1'])
        state.append(j['location']['state'])
        zip_code.append(j['location']['zip_code'])
        country.append(j['location']['country'])

In [6]:
#for price 
price=[]
for i in b_data:
    for j in i['businesses']:
        if 'price' in j.keys():
            len(j['price'])
            price.append(len(j['price']))       
        else:
            None 
            price.append(None)
len(price)

1000

In [7]:
#for phone
phone=[]
for i in b_data:
    for j in i['businesses']:
        if 'phone' in j.keys():
            j['phone']
            phone.append(j['phone'])       
        else:
            None 
            phone.append(None)
len(phone)


1000

In [8]:
def reviewCallGET(id_num):
    reviewEndpoint_base = 'https://api.yelp.com/v3/businesses/'
    reviewEndpoint_end = '/reviews'
    return {id_num:requests.get(reviewEndpoint_base + id_num + reviewEndpoint_end,headers=headers).json()}

In [9]:
# for i in review_data ['id', 'text', 'rating', 'time_created', 'user']
review=[]
for i in business_id:
    review.append(reviewCallGET(i))
                                
review   

[{'ysqgdbSrezXgVwER2kQWKA': {'reviews': [{'id': '6KxoyzoOcO61gIGFUt76ag',
     'url': 'https://www.yelp.com/biz/julianas-pizza-brooklyn-5?adjust_creative=H-RlZ0bPhg3dmTEOOsLJMg&hrid=6KxoyzoOcO61gIGFUt76ag&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_reviews&utm_source=H-RlZ0bPhg3dmTEOOsLJMg',
     'text': "Ate here once last year and came back again today! Now that I moved to NYC, I'm definitely ready to go back whenever. Party of 4 came on Saturday night at...",
     'rating': 5,
     'time_created': '2020-01-26 19:50:38',
     'user': {'id': '4pCLAHH-z6hZl_9q-4_UAg',
      'profile_url': 'https://www.yelp.com/user_details?userid=4pCLAHH-z6hZl_9q-4_UAg',
      'image_url': 'https://s3-media2.fl.yelpcdn.com/photo/N-CDH3eAFLeQN7VkW4U6Sg/o.jpg',
      'name': 'Judy L.'}},
    {'id': 'GItqAWpYoGQZu-lMuqJmFg',
     'url': 'https://www.yelp.com/biz/julianas-pizza-brooklyn-5?adjust_creative=H-RlZ0bPhg3dmTEOOsLJMg&hrid=GItqAWpYoGQZu-lMuqJmFg&utm_campaign=yelp_api_v3&utm_medium=api_v3_b

In [10]:
review_data=review.copy()


In [11]:
business_id_review_id=[]
for i in range(0,len(review_data)):
        for m in range(0,len(review_data[i][business_id[i]]['reviews'])):
            business_id_review_id.append((business_id[i],review_data[i][business_id[i]]['reviews'][m]['id']))
business_id_R=[]            
for i in business_id_review_id:
    business_id_R.append(i[0])
    
review_id=[]
for i in business_id_review_id:
    review_id.append(i[1])

In [12]:
#review_data--text
text=[]
for i in range(0,len(review_data)):
        for m in range(0,len(review_data[i][business_id[i]]['reviews'])):
            text.append(review_data[i][business_id[i]]['reviews'][m]['text'])
len(text)

2974

In [13]:
review_rating=[]
for i in range(0,len(review_data)):
        for m in range(0,len(review_data[i][business_id[i]]['reviews'])):
            review_rating.append(review_data[i][business_id[i]]['reviews'][m]['rating'])
len(review_rating)

2974

In [14]:
user=[]
for i in range(0,len(review_data)):
        for m in range(0,len(review_data[i][business_id[i]]['reviews'])):
            user.append(review_data[i][business_id[i]]['reviews'][m]['user'])
            
users=[]            
for i in range(0,len(user)):
    users.append(user[i]['name'])
len(users)

2974

In [15]:
time_created = []
for i in range(0,len(review_data)):
        for m in range(0,len(review_data[i][business_id[i]]['reviews'])):
            time_created.append(review_data[i][business_id[i]]['reviews'][m]['time_created'])
len(time_created)


2974

In [16]:
reviews=[]
for i in range(0,len(review_id)):
     reviews.append((review_id[i], text[i], review_rating[i], users[i], time_created[i], business_id_R[i]))

In [17]:
reviews

[('6KxoyzoOcO61gIGFUt76ag',
  "Ate here once last year and came back again today! Now that I moved to NYC, I'm definitely ready to go back whenever. Party of 4 came on Saturday night at...",
  5,
  'Judy L.',
  '2020-01-26 19:50:38',
  'ysqgdbSrezXgVwER2kQWKA'),
 ('GItqAWpYoGQZu-lMuqJmFg',
  'We heard about the story of Juliana so we had to come try it! After walking the whole bridge we were ready to eat! \nWhen we got there, there was a line......',
  5,
  'Shelly C.',
  '2020-01-14 14:33:08',
  'ysqgdbSrezXgVwER2kQWKA'),
 ('07fSxrTbYkFzSeJC9IpmWw',
  "I've tried and ranked a lot of pizza places in New York City and this is by far the easiest 5/5 star and my favorite pizza in all of NYC. The pizza is so...",
  5,
  'Sabrina P.',
  '2020-01-09 19:24:39',
  'ysqgdbSrezXgVwER2kQWKA'),
 ('H4eanmM_xB5MESW0vYWXlQ',
  'Every time you go by here, there is a line out the door. Dont be fooled as there is nowhere inside to stand inside!  That is the catch right?  Long lines...',
  5,
  'Erik H.'

In [41]:
# checking for duplicates
for i in review_id:
        if review_id.count(i)>1:
            print(i)

In [19]:
len(business_id)

1000

In [20]:
# #b_data
# business_id
# name
# review_count
# rating
# street
# state
# zip_code
# country
# price
# phone
business_1=[]
for i in range(0,len(business_id)):
     business_1.append((business_id[i],name[i],price[i],phone[i],review_count[i],rating[i],street[i],
                       state[i],zip_code[i],country[i]))

In [25]:
import mysql.connector 
from mysql.connector import errorcode
# cnx = mysql.connector.connect(
#     host = 'database-1.cmro5o0wbrvi.us-east-2.rds.amazonaws.com',
#     user = 'admin',
#     passwd = 'K3yb0ard!')

In [ ]:
# checking for duplicates
for i in business_id:
        if business_id.count(i)>1:
            print(i)

In [22]:
db_name = 'yelp'
TABLES = {}
# TABLES['businesses'] = (
#     "CREATE TABLE businesses ("
#     "  business_id varchar(200) NOT NULL ,"
#     "  name varchar(200),"
#     "  review_count int(250),"
#     "  rating DECIMAL (10,2) ,"
#     "  price int(10),"
#     "  phone varchar(200),"
#     "  street varchar(200),"
#     "  city varchar(200),"
#     "  zip_code int(5),"
#     "  state varchar(200),"
#     "  country varchar(200) ,"
#     "  PRIMARY KEY (business_id)"
#     ")")
# business_id_R
#review_id 
# text
# rating 
# user
# time_created
# review_id[i],text[i],review_rating[i],users[i],time_created[i], business_id_R[i])
TABLES['reviews'] = (
    "CREATE TABLE reviews ("
    "  review_id varchar(200) NOT NULL,"
    "  text varchar(5000) ,"
    "  rating char(4)  ,"
    "  user varchar(14),"
    "  time_created varchar (50)"
    "  business_id varchar(200) ,"
    "  PRIMARY KEY (review_id)"
    ")")

In [ ]:
def create_database(cursor, database):
    try:
        cursor.execute(
            "CREATE DATABASE {} DEFAULT CHARACTER SET 'utf8'".format(database))
    except mysql.connector.Error as err:
        print("Failed creating database: {}".format(err))
        exit(1)

In [ ]:
cursor = cnx.cursor()
try:
    cursor.execute("USE {}".format(db_name))

#if the previous line fails because there isn't a db by that name run this line

except mysql.connector.Error as err:
    print("Database {} does not exists.".format(db_name))
    if err.errno == errorcode.ER_BAD_DB_ERROR:
        create_database(cursor, db_name)
        print("Database {} created successfully.".format(db_name))
        cnx.database = db_name
    else:
        print(err)
        exit(1)

In [33]:
cnx = mysql.connector.connect(
    host = 'database-1.cmro5o0wbrvi.us-east-2.rds.amazonaws.com',
    user = 'admin',
    passwd = 'K3yb0ard!',
    database = db_name
)
cursor = cnx.cursor()

In [27]:
for table_name in TABLES:
    table_description = TABLES[table_name]
    try:
        print("Creating table {}: ".format(table_name), end='')
        cursor.execute(table_description)
    except mysql.connector.Error as err:
        if err.errno == errorcode.ER_TABLE_EXISTS_ERROR:
            print("already exists.")
        else:
            print(err.msg)
    else:
        print("OK")

Creating table reviews: You have an error in your SQL syntax; check the manual that corresponds to your MySQL server version for the right syntax to use near 'business_id varchar(200) ,  PRIMARY KEY (review_id))' at line 1


In [30]:
# adding time created
cursor.execute("""ALTER TABLE yelp.reviews
                ADD COLUMN time_created varchar (50)""")

In [ ]:
stmt="INSERT INTO businesses(business_id, name, price, phone, review_count, rating, street, state, zip_code, country) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s)"

In [ ]:
cursor.executemany(stmt, business_1)
cnx.commit()

In [47]:
stmr2 = "INSERT INTO reviews('time_created') VALUES(%s)"

In [39]:
stmr = "INSERT INTO reviews(review_id, text, rating, uesr, time_created, business_id) VALUES (%s, %s, %s, %s, %s, %s)" 

In [52]:
cursor.execute("INSERT INTO reviews(time_created) VALUES(%s);")
cnx.commit()

ProgrammingError: 1064 (42000): You have an error in your SQL syntax; check the manual that corresponds to your MySQL server version for the right syntax to use near '%s)' at line 1

In [ ]:
cursor.close()
cnx.close()

## Part 3 - Create ETL pipeline for the business data from the API

Now that you know what data you need from the API, you want to write code that will execute a api call, parse those results and then insert the results into the DB.  

It is helpful to break this up into three different functions (*api call, parse results, and insert into DB*) and then you can write a function/script that pull the other three functions together. 

Let's first do this for the Business endpoint.

In [ ]:
# Write a function to make a call to the yelp API

In [ ]:
# write a function to parse the API response 
# so that you can easily insert the data in to the DB

In [ ]:
# Write a function to take your parsed data and insert it into the DB

In [ ]:
# Write a script that combines the three functions above into a single process.

## Part 4 -  Create ETL pipeline for the restaurant review data from the API

You've done this for the Businesses, now you need to do this for reviews. You will follow the same process, but your functions will be specific to reviews.

In [ ]:
# write a SQL query to pull back all of the business ids 
# you will need these ids to pull back the reviews for each restaurant

In [ ]:
# write a function that takes a business id 
# and makes a call to the API for reivews


In [ ]:
# Write a function to parse out the relevant information from the reviews

In [ ]:
# write a function to insert the parsed data into the reviews table

In [ ]:
# combine the functions above into a single script  

## Part 5 -  Write SQL queries that will answer the questions posed. 

Now that your data is in the DB, you can answer the questions. Write SQL querires that will answer the questions. **Do not use Pandas in this lab**

In [ ]:
# create connection

In [ ]:
# execute SQL queries

# Extra Reference help

###  Pagination

Returning to the Yelp API, the [documentation](https://www.yelp.com/developers/documentation/v3/business_search) also provides us details regarding the API limits. These often include details about the number of requests a user is allowed to make within a specified time limit and the maximum number of results to be returned. In this case, we are told that any request has a maximum of 50 results per request and defaults to 20. Furthermore, any search will be limited to a total of 1000 results. To retrieve all 1000 of these results, we would have to page through the results piece by piece, retriving 50 at a time. Processes such as these are often refered to as pagination.

Now that you have an initial response, you can examine the contents of the json container. For example, you might start with ```response.json().keys()```. Here, you'll see a key for `'total'`, which tells you the full number of matching results given your query parameters. Write a loop (or ideally a function) which then makes successive API calls using the offset parameter to retrieve all of the results (or 5000 for a particularly large result set) for the original query. As you do this, be mindful of how you store the data. 

**Note: be mindful of the API rate limits. You can only make 5000 requests per day, and APIs can make requests too fast. Start prototyping small before running a loop that could be faulty. You can also use time.sleep(n) to add delays. For more details see https://www.yelp.com/developers/documentation/v3/rate_limiting.**

***Below is sample code that you can use to help you deal with the pagination parameter and bring all of the functions together.***


***Also, something might cause your code to break while it is running. You don't want to constantly repull the same data when this happens, so you should insert the data into the database as you call and parse it, not after you have all of the data***


In [ ]:
def yelp_call(url_params, api_key):
    # your code to make the yelp call
    return data

In [ ]:
def parse_results(results):
    # your code to parse the result to make them easier to insert into the DB
    return parsed_results

In [ ]:
def db_insert(cnx, cursor, parsed results):
    # your code to insert and commit the results
    # I would create the connection and cursor outside of this function and then pass it through

In [ ]:
# create a variable  to keep track of which result you are in. 
cur = 0

#set up a while loop to go through and grab the result 
while cur < num and cur < 1000:
    #set the offset parameter to be where you currently are in the results 
    url_params['offset'] = cur
    #make your API call with the new offset number
    results = yelp_call(url_params, api_key)
    
    #after you get your results you can now use your function to parse those results
    parsed_results = parse_results(results)
    
    # use your function to insert your parsed results into the db
    db_insert(parsed_results)
    #increment the counter by 50 to move on to the next results
    cur += 50